
File: 09-lecture_solution.py


Michel Bierlaire

Fri Aug 23 18:35:24 2024



In [ ]:

from IPython.core.display_functions import display
import biogeme.biogeme_logging as blog
from biogeme.biogeme import BIOGEME
from biogeme.expressions import Beta, log, exp, bioDraws, MonteCarlo
from biogeme.models import loglogit, logit
from biogeme.results import compile_estimation_results, bioResults


Variables used for the specification of the Swissmetro model are defined in the file `swissmetro_variables.py`.

In [ ]:
from swissmetro_variables import (
    database,
    CHOICE,
    TRAIN_AV_SP,
    SM_AV,
    CAR_AV_SP,
    TRAIN_TT_SCALED,
    TRAIN_COST_SCALED,
    TRAIN_HE_SCALED,
    SM_TT_SCALED,
    SM_COST_SCALED,
    SM_HE_SCALED,
    CAR_TT_SCALED,
    CAR_CO_SCALED,
    MALE,
    GA,
    BUSINESS,
    LOW_INC,
    FIRST,
)


As the estimation time may be long, we ask Biogeme to report the details of the iterations.

In [ ]:
logger = blog.get_screen_logger(level=blog.INFO)


**Tip:**<div class="alert alert-block alert-info">It is advised to start working with a low number of draws,
until the script is working well. Then, increase the number of draws to 10000, say. Then, execute the script
overnight.  </div>

In [ ]:
number_of_draws = 10



# Parameters

In [ ]:
asc_car = Beta('asc_car', 0, None, None, 0)
asc_train = Beta('asc_train', 0, None, None, 0)
b_time = Beta('b_time', 0, None, None, 0)
b_cost = Beta('b_cost', 0, None, None, 0)
b_fr = Beta('b_fr', 0, None, None, 0)



# Availability conditions

In [ ]:
av = {1: TRAIN_AV_SP, 2: SM_AV, 3: CAR_AV_SP}



# Logit model

## Utility functions

In [ ]:
V1 = (
    asc_train
    + b_time * TRAIN_TT_SCALED
    + b_cost * TRAIN_COST_SCALED
    + b_fr * TRAIN_HE_SCALED
)
V2 = b_time * SM_TT_SCALED + b_cost * SM_COST_SCALED + b_fr * SM_HE_SCALED
V3 = asc_car + b_time * CAR_TT_SCALED + b_cost * CAR_CO_SCALED
V = {1: V1, 2: V2, 3: V3}



## Model

In [ ]:
logprob = loglogit(V, av, CHOICE)



## Estimation

In [ ]:
biogeme = BIOGEME(database, logprob)
biogeme.modelName = '01logit'
results_logit = biogeme.estimate(recycle=True)



## Results

General statistics

In [ ]:
print(results_logit.print_general_statistics())


Estimated parameters

In [ ]:
param_logit = results_logit.get_estimated_parameters()
display(param_logit)



# Random parameter: normal distribution

Read the results from file

In [ ]:
results_normal = bioResults(pickle_file='02normal.pickle')



# Random parameter: lognormal distribution

Read the results from file

In [ ]:
results_lognormal = bioResults(pickle_file='03lognormal.pickle')



# Latent classes

Read the results from file

In [ ]:
results_latent = bioResults(pickle_file='04latentClass.pickle')



# Latent classes with class membership model

Read the results from file

In [ ]:
results_latentsocio = bioResults(pickle_file='05latentClass.pickle')



# Latent classes with random parameter

We consider again two classes in the population. The first class of individuals have considered all variables
when making their choice. For them, the specification of the utility function is the same as for the logit model,
where the time coefficient is now distributed in the population.

In [ ]:
b_time_s = Beta('b_time_s', 1, None, None, 0)
b_time_rnd = b_time + b_time_s * bioDraws('b_time_rnd', 'NORMAL')


Utility function, class 1

In [ ]:
V1_class_1 = (
    asc_train
    + b_time_rnd * TRAIN_TT_SCALED
    + b_cost * TRAIN_COST_SCALED
    + b_fr * TRAIN_HE_SCALED
)
V2_class_1 = b_time * SM_TT_SCALED + b_cost * SM_COST_SCALED + b_fr * SM_HE_SCALED
V3_class_1 = asc_car + b_time * CAR_TT_SCALED + b_cost * CAR_CO_SCALED
V_class_1 = {1: V1_class_1, 2: V2_class_1, 3: V3_class_1}



The second class of individuals ignored the travel time variable when making the choice. Therefore, this variable
is removed from the utility function.

In [ ]:
V1_class_2 = asc_train + b_cost * TRAIN_COST_SCALED + b_fr * TRAIN_HE_SCALED
V2_class_2 = b_cost * SM_COST_SCALED + b_fr * SM_HE_SCALED
V3_class_2 = asc_car + b_cost * CAR_CO_SCALED
V_class_2 = {1: V1_class_2, 2: V2_class_2, 3: V3_class_2}



The following parameters are involved in the class membership model.

In [ ]:
g_intercept = Beta('g_intercept', 0, None, None, 0)
g_male = Beta('g_male', 0, None, None, 0)
g_ga = Beta('g_ga', 0, None, None, 0)
g_business = Beta('g_business', 0, None, None, 0)
g_low_inc = Beta('g_low_inc', 0, None, None, 0)
G_FIRST = Beta('G_FIRST', 0, None, None, 0)



Class membership model. Note that `omega` can potentially take any real value. We have to transform it into a
probability using the transform `1 / (1 + exp(omega))`

In [ ]:
omega = (
    g_intercept
    + g_male * MALE
    + g_ga * GA
    + g_business * BUSINESS
    + g_low_inc * LOW_INC
    + G_FIRST * FIRST
)
prob_class_1 = 1 / (1 + exp(omega))
prob_class_2 = 1 - prob_class_1



## Model

We first calculate the choice probability for each class.

In [ ]:
cond_choice_prob_class_1 = logit(V_class_1, av, CHOICE)
choice_prob_class_1 = MonteCarlo(cond_choice_prob_class_1)
choice_prob_class_2 = logit(V_class_2, av, CHOICE)



The choice probability is obtained by using the class membership model.

In [ ]:
prob = prob_class_1 * choice_prob_class_1 + prob_class_2 * choice_prob_class_2
logprob = log(prob)



## Estimation

In [ ]:
biogeme = BIOGEME(database, logprob, number_of_draws=number_of_draws)
biogeme.modelName = '06mixedLatentClass'
results_latentrandom = biogeme.estimate()



## Results

General statistics

In [ ]:
print(results_latentrandom.print_general_statistics())


Estimated parameters

In [ ]:
param_latentrandom = results_latentrandom.get_estimated_parameters()
display(param_latentrandom)



# Comparison

We build a summary data frame. We first gather the parameter estimates for each model.

In [ ]:
summary = compile_estimation_results(
    {
        'Logit': results_logit,
        'Random param. (normal)': results_normal,
        'Random param. (lognormal)': results_lognormal,
        'Latent class': results_latent,
        'Latent class with class mbship': results_latentsocio,
        'Latent with random param.': results_latentrandom,
    }
)
display(summary[0])